In [66]:
import numpy as np
import pandas as pd
import os
import tensorflow as tf
from PIL import Image
import sys
from tqdm import tqdm

from tensorflow.train import BytesList, FloatList, Int64List
from tensorflow.train import Example, Features, Feature

In [67]:
DATASET_PATH  = './Dataset 2/'

In [68]:
# Getting data from different folders in dataset
# with respective category and saving it in Dataframe
#mount drive to get data


DATA_CATEGORY = ['covid', 'non-covid']


df = pd.DataFrame(columns=['images','label', 'height', 'width', 'Format', 'mode'])

for cat in DATA_CATEGORY:
        cat_path = os.path.join(DATASET_PATH, cat)
        for image_file in tqdm(os.listdir(cat_path), desc=cat +' Reading data...'):
            image_path = os.path.join(cat_path, image_file)
            image = Image.open(image_path)
            img_arr = np.asarray(image)
            df.loc[len(df.index)] = [img_arr, cat, image.size[0], image.size[1], image.format, image.mode]

df.info()

non-covid Reading data...: 100%|██████████████████████████████████████████████████| 1626/1626 [00:14<00:00, 110.88it/s]

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3227 entries, 0 to 3226
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   images  3227 non-null   object
 1   label   3227 non-null   object
 2   height  3227 non-null   object
 3   width   3227 non-null   object
 4   Format  3227 non-null   object
 5   mode    3227 non-null   object
dtypes: object(6)
memory usage: 176.5+ KB


In [11]:
# label = {0:0, 2:1}

# train_df = pd.read_csv(DATASET_PATH + '/train_COVIDx_CT-2A.txt', delimiter=' ',  names=['file', 'label', 'xmin', 'ymin', 'xmax', 'ymax'])
# test_df = pd.read_csv(DATASET_PATH + '/test_COVIDx_CT-2A.txt', delimiter=' ', names=['file', 'label', 'xmin', 'ymin', 'xmax', 'ymax'])
# val_df = pd.read_csv(DATASET_PATH + '/val_COVIDx_CT-2A.txt', delimiter=' ', names=['file', 'label', 'xmin', 'ymin', 'xmax', 'ymax'])

# train_df = train_df[train_df['label'] != 1]
# train_df['label'] = train_df['label'].replace(label)
# train_df['label'] = train_df['label'].astype('int')
# train_df = train_df.drop(['xmin', 'ymin', 'xmax', 'ymax'], axis=1)

# test_df = test_df[test_df['label'] != 1]
# test_df['label'] = test_df['label'].replace(label)
# test_df['label'] = test_df['label'].astype('int')
# test_df = test_df.drop(['xmin', 'ymin', 'xmax', 'ymax'], axis=1)

# val_df = val_df[val_df['label'] != 1]
# val_df['label'] = val_df['label'].replace(label)
# val_df['label'] = val_df['label'].astype('int')
# val_df = val_df.drop(['xmin', 'ymin', 'xmax', 'ymax'], axis=1)

In [70]:
df['label'] = df['label'].replace({'covid':1, 'non-covid':0})

df.head()

images  label height width  \
0  [[[255, 255, 255, 255], [251, 251, 251, 255], ...      1    580   335   
1  [[[66, 66, 66, 255], [72, 72, 72, 255], [79, 7...      1    566   332   
2  [[[218, 218, 218, 255], [221, 221, 221, 255], ...      1    612   366   
3  [[[45, 45, 45, 255], [43, 43, 43, 255], [41, 4...      1    725   551   
4  [[[44, 44, 44, 255], [45, 45, 45, 255], [46, 4...      1    720   541   

  Format  mode  
0    PNG  RGBA  
1    PNG  RGBA  
2    PNG  RGBA  
3    PNG  RGBA  
4    PNG  RGBA

In [46]:
# def _data_path(data_directory, name):
#     if not os.path.isdir(data_directory):
#         os.makedirs(data_directory)

#     return os.path.join(data_directory, f'{name}.tfrecords')

# def _int64_feature(value):
#     return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))

# def _bytes_feature(value):
#     return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))

# def convert_to(data_set, name, data_directory, num_shards):
#     print(f'Processing {name} data')

#     images = data_set.images
#     labels = data_set.label
    
#     def _process_examples(start_idx, end_index, filename):
#         with tf.io.TFRecordWriter(filename) as writer:
#             for index in range(start_idx, end_index):
#                     sys.stdout.write(f"\rProcessing sample {index+1} of {end_index}")
#                     sys.stdout.flush()

# #                     image_raw = np.array(Image.open(os.path.join(DATASET_PATH, '2A_images', images[index]))).tobytes()
#                     image_raw = images[index].tobytes()
#                     example = tf.train.Example(features=tf.train.Features(feature={
#                         'class': _int64_feature(int(labels[index])),
#                         'image': _bytes_feature(image_raw)
#                     }))
#                     #print(example)
#                     writer.write(example.SerializeToString())
    
#     if num_shards == 1:
#         _process_examples(0, len(data_set), _data_path(data_directory, name))
#     else:
#         total_examples = len(data_set)
#         samples_per_shard = total_examples // num_shards

#         for shard in range(num_shards):
#             start_index = shard * samples_per_shard
#             end_index = start_index + samples_per_shard
#             _process_examples(start_index, end_index, _data_path(data_directory, f'{name}-{shard+1}'))

#     print()
    
    
# def convert_to_tf_record(data_directory):  
# #     convert_to(train_df, 'train', data_directory, num_shards=8)
# #     convert_to(val_df, 'validation', data_directory, num_shards=1)
# #     convert_to(test_df, 'test', data_directory, 1)
#     convert_to(df, 'train', data_directory, 8)

In [93]:
def _int64_feature(value):
    return tf.train.Feature(int64_list=tf.train.Int64List(value=[value]))

def _bytes_feature(value):
    return tf.train.Feature(bytes_list=tf.train.BytesList(value=[value]))

def get_example_object(data_record):
    
    # Create a dictionary with above lists individually wrapped in Feature
    feature_key_value_pair = {
        'image': _bytes_feature(data_record['images'].tobytes()),
        'label':_int64_feature(int(data_record['label']))
    }
    
    features = tf.train.Features(feature = feature_key_value_pair)
    example = tf.train.Example(features = features)
    return example

def write_file(filename, save_dir, dataset):
    with tf.io.TFRecordWriter(os.path.join(save_dir, filename+'.tfrecord')) as tfwriter:
        for i, data_record in dataset.iterrows():
            sys.stdout.write(f"\rProcessing sample {i} of {len(dataset)}")
            sys.stdout.flush()
            example = get_example_object(data_record)
            tfwriter.write(example.SerializeToString())

                        
def convert_to(dataset, save_dir, filename, shards=1):
    if shards == 1:
        write_file(filename,save_dir, dataset)
    else:
        total_examples = len(dataset)
        samples_per_shard = total_examples // shards

        for shard in range(shards):
            start_index = shard * samples_per_shard
            end_index = min(start_index + samples_per_shard, total_examples)
            data = dataset.iloc[start_index:end_index, :]
            write_file(f'{filename}-{shard+1}', save_dir, data)

In [94]:
convert_to(df.copy(), './TF_DATASET_2','images', shards=8)

Processing sample 3223 of 403

In [116]:
def decode_fn(record_bytes):
  return tf.io.parse_single_example(
      record_bytes,
      {"label": tf.io.FixedLenFeature([], dtype=tf.int64),
       "image": tf.io.FixedLenFeature([], dtype=tf.string)}
  )

In [119]:
import tensorflow as tf 
import glob


dataset = tf.data.TFRecordDataset(['./TF_DATASET_2/images-1.tfrecord'])
dataset = dataset.map(decode_fn)

print(dataset)

for i, data in enumerate(dataset):
    example = decode_fn(data)
    print(example)
#     sys.stdout.write(f"\rProcessing sample {i}")
#     sys.stdout.flush()
    break

<MapDataset shapes: {image: (), label: ()}, types: {image: tf.string, label: tf.int64}>


ValueError: Attempt to convert a value ({'image': <tf.Tensor: shape=(), dtype=string, numpy=b'\xff\xff\xff\xff\xfb\xfb\xfb\xff\xf0\xf0\xf0\xff\xe5\xe5\xe5\xff\xdd\xdd\xdd\xff\xd8\xd8\xd8\xff\xd5\xd5\xd5\xff\xd3\xd3\xd3\xff\xd2\xd2\xd2\xff\xd1\xd1\xd1\xff\xd1\xd1\xd1\xff\xd2\xd2\xd2\xff\xd3\xd3\xd3\xff\xd3\xd3\xd3\xff\xd4\xd4\xd4\xff\xd5\xd5\xd5\xff\xd3\xd3\xd3\xff\xd2\xd2\xd2\xff\xd0\xd0\xd0\xff\xcd\xcd\xcd\xff\xca\xca\xca\xff\xc9\xc9\xc9\xff\xcb\xcb\xcb\xff\xcd\xcd\xcd\xff\xd2\xd2\xd2\xff\xd1\xd1\xd1\xff\xd1\xd1\xd1\xff\xd3\xd3\xd3\xff\xd5\xd5\xd5\xff\xd2\xd2\xd2\xff\xd0\xd0\xd0\xff\xd0\xd0\xd0\xff\xd0\xd0\xd0\xff\xd2\xd2\xd2\xff\xd4\xd4\xd4\xff\xd5\xd5\xd5\xff\xd5\xd5\xd5\xff\xd3\xd3\xd3\xff\xd1\xd1\xd1\xff\xcf\xcf\xcf\xff\xce\xce\xce\xff\xd0\xd0\xd0\xff\xd2\xd2\xd2\xff\xd2\xd2\xd2\xff\xd0\xd0\xd0\xff\xcd\xcd\xcd\xff\xca\xca\xca\xff\xc8\xc8\xc8\xff\xc7\xc7\xc7\xff\xc8\xc8\xc8\xff\xca\xca\xca\xff\xce\xce\xce\xff\xd3\xd3\xd3\xff\xd8\xd8\xd8\xff\xdc\xdc\xdc\xff\xde\xde\xde\xff\xdf\xdf\x

In [28]:
import tensorflow as tf

for example in ("./TF_DATASET_2/train-1.tfrecord"):
    print(tf.train.Example.FromString(example))

AttributeError: module 'tensorflow._api.v2.io' has no attribute 'tf_record_iterator'